In [1]:
import os

os.chdir("../")
os.getcwd()

'c:\\Users\\HP\\Desktop\\DS_DL\\pygcn'

In [2]:
# load data
from pygcn.utils import load_data

adj, features, labels, idx_train, idx_val, idx_test = load_data(
    path="./data/cora/"
)

Loading cora dataset...


In [3]:
# setups
from pygcn.models import GCN
import torch.optim as optim


# define model
model = GCN(
    nfeat=features.shape[1],
    # paper uses 32 hidden units
    nhid=32,
    nclass=labels.max().item() + 1,
    # no dropout in paper
    dropout=0
)

# setup optimizer
optimizer = optim.Adam(
    model.parameters(),
    lr=0.01, 
    # weight_decay=args.weight_decay
)

In [4]:
# data structure  frames
# to save frames

frames = {
    "x": [],
    "y": [],
    "labels": [],
    "epoch": []
}

In [5]:
import torch.nn.functional as F
from sklearn.manifold import TSNE

from pygcn.utils import accuracy


# params
range_features = range(features.shape[0])
arr_loss_train = []


def train(epoch):
    # set train phase
    model.train()
    optimizer.zero_grad()

    # forward
    output = model(features, adj)
    # train
    loss_train = F.nll_loss(output[idx_train], labels[idx_train])
    acc_train = accuracy(output[idx_train], labels[idx_train])
    # validation
    loss_val = F.nll_loss(output[idx_val], labels[idx_val])
    acc_val = accuracy(output[idx_val], labels[idx_val])

    # backward
    loss_train.backward()
    optimizer.step()

    # 
    arr_loss_train.append(loss_train.item())

    # save only 1 / 5 epochs
    if epoch % 10 == 0:
        # reduce and save
        XY = reduce_embeddings(model)

        # save into frames
        frames["x"] += list(XY[:, 0])
        frames["y"] += list(XY[:, 1])
        frames["labels"] += list(labels.numpy().astype(str))
        frames["epoch"] += [epoch for i in range_features]

    return


def reduce_embeddings(model):
    embedding_model = list(model.children())[0]
    X = embedding_model(features, adj).detach().numpy()

    X_embedded = TSNE(
        n_components=2, 
        learning_rate='auto',
        init='random'
        ).fit_transform(X)

    return X_embedded


In [6]:
import tqdm

# training loop
MAX_NB_EPOCHS = 110

for epoch in tqdm.tqdm(range(MAX_NB_EPOCHS + 1)):
    train(epoch)

100%|██████████| 111/111 [04:30<00:00,  2.44s/it]


In [7]:
import pandas as pd
import plotly.express as px


frames_df = pd.DataFrame(frames)

fig = px.scatter(
    frames_df,
    x="x",
    y="y",
    color="labels",
    animation_frame="epoch"
)

fig.update_layout(
    title="Animation of nodes representations"
)

fig.show(renderer="notebook")